# Кейс "ИИ-инструмент работы с данными перспективной городской застройки" 
от ```Государственного казенного учреждения города Москвы - Центра организации дорожного движения Правительства Москвы```!

***
## Описание датасета
Архив с исходными данными содержит в себе:
1) Данные в формате shp (векторный формат пространственных данных)
2) Описание атрибутивного состава исходных данных: ```ЦОДД_описание атрибутов.docx```
Данные включают в себя 6 типов файлов, хранящих информацию о 4 пространственных линейных слоях (исходные улицы, исходные дома, а также 1, 2 и 3 очередь их постройки; остановки ОТ и выходы метро):
- ```.shp``` - Это файл в формате shape.
- ```.shx``` — Это файл индекса для файлов формата Shapefile (.shp), который используется для хранения векторных данных. Он содержит информацию о том, где расположены объекты в файле .shp.
- ```.qmd``` — Это файл проекта Quarto, который используется для создания документов и отчетов в формате Markdown. Quarto — это инструмент для динамического создания отчетов и публикаций. В Python вы можете просто открыть .qmd как текстовый файл для чтения
- ```.prj``` — Этот файл содержит информацию о системе координат и проекции, используемой для данных в Shapefile. Он описывает географическую область, к которой относятся данные.
- ```.dbf``` — Это файл базы данных, который хранит атрибутные данные для объектов, описанных в файлах .shp. Он используется в сочетании с Shapefile для хранения информации о каждом пространственном объекте.
- ```.cpg``` — Этот файл используется для указания кодировки символов, используемой в файле .dbf, чтобы корректно отображать текстовые данные.

В случае, если на месте перспективного ЖК в настоящее время расположены сторонние здания - они должны быть удалены. Необходимо соблюдать версионность дорожного графа (пешеходных дорожек), если ИИ предложит альтернативную схему расположения пешеходных дорожек, то эту версию считаем основной и при дальнейшем анализе новых данных необходимо брать в расчет данные ИИ.
***
Необходимо создать инструмент с применением ИИ, который позволит принимать эффективные решения при строительстве жилых комплексов в части улучшения движения транспорта и пешеходов.

In [1]:
# %pip install numpy==1.23.5 numba==0.60.0 geopandas==1.0.1 folium==0.18.0 matplotlib==3.9.2 mapclassify==2.8.1

In [43]:
import networkx as nx
import folium
import geopandas as gpd
import pandas as pd
from shapely import affinity
from shapely.geometry import (
    LineString,
    MultiPoint,
    MultiPolygon,
    Point,
    Polygon,
    mapping,
)
from shapely.ops import nearest_points

import warnings
warnings.filterwarnings("ignore")

import os

# os.listdir('data')

In [19]:
gdf_ОТ = pd.concat([
    gpd.read_file("data/Выходы_метро.dbf").assign(TrType='Выходы_метро').rename(columns={'Text': 'Name'}),
    gpd.read_file("data/Остановки_ОТ.dbf"),
], ignore_index=True).to_crs(epsg=2584)[['TrType', 'Name', 'geometry']]

gdf_house = pd.concat([
    gpd.read_file("data/Дома_исходные.dbf").assign(ver=0),
    gpd.read_file("data/House_1очередь_ЖК.dbf").assign(ver=1),
    gpd.read_file("data/House_2очередь_ЖК.dbf").assign(ver=2),
    gpd.read_file("data/House_3очередь_ЖК.dbf").assign(ver=3),
], ignore_index=True).to_crs(epsg=2584)[['ver', 'Type', 'Purpose', 'Apartments', 'geometry']]
gdf_house = gdf_house[(gdf_house['Apartments']>0)|(gdf_house['Type'].isin(['Жилые дома', 'Школы', 'Административные сооружения', 'Дошкольные', 'Частные дома', 'Дома_новостройки']))]
gdf_house['Code_Type'] = gdf_house.apply(lambda x: 2 if x['Type'] in ['Школы', 'Дошкольные'] else 1 if x['Apartments']>0 else 0, axis=1)
gdf_house = gdf_house.drop_duplicates('geometry')

gdf_streets = pd.concat([
    gpd.read_file("data/Streets_исходные.dbf").assign(ver=0),
    gpd.read_file("data/Streets_1очередь.dbf").assign(ver=1),
    gpd.read_file("data/Streets_2очередь.dbf").assign(ver=2),
    gpd.read_file("data/Streets_3очередь.dbf").assign(ver=3),
], ignore_index=True).to_crs(epsg=2584)[['ver', 'ROAD_CATEG', 'Foot', 'length', 'geometry']]
gdf_streets = gdf_streets[gdf_streets["Foot"]>0]
gdf_streets = gdf_streets.drop_duplicates('geometry')

# Ограничиваем область, убираем выбросы, оставляем только остановки, здания, дороги 2 км (30 минут) от новых очередей
work_area = gdf_house[gdf_house.ver>0].dissolve().convex_hull.buffer(2000)
gdf_ОТ = gdf_ОТ[gdf_ОТ.centroid.intersects(work_area.item())]
gdf_house = gdf_house[gdf_house.centroid.intersects(work_area.item())]
gdf_streets = gdf_streets[gdf_streets.centroid.intersects(work_area.item())]


In [70]:
# Стороим сеть для формирования новых дорожек

minx, miny, maxx, maxy = gdf_house[gdf_house.ver>0].dissolve().buffer(200).item().bounds

slice_x = 0
slice_y = 0

param_step = 25

grid_x = []
x = minx + slice_x
while x < maxx:
    grid_x += [x]
    x += param_step

grid_y = []
y = miny + slice_y
while y < maxy:
    grid_y += [y]
    y += param_step

full_grid_xy = (gdf_house[gdf_house.ver>0].dissolve().buffer(200)
                .intersection(MultiPoint([(x,y) for x in grid_x for y in grid_y]))
                .difference(gdf_house.convex_hull.make_valid().union_all().buffer(15))               )


In [71]:
m = folium.Map(location=(55.755826, 37.6173), zoom_start=9, attributionControl=0)

folium.TileLayer("CartoDB positron", name="CartoDB positron").add_to(m)
folium.TileLayer(
    "https://mt0.google.com/vt/lyrs=m&hl=ru&x={x}&y={y}&z={z}",
    attr="Google Roadmap",
    name="Google Схема",
).add_to(m)

fg = folium.FeatureGroup(name="До 2 км от новых очередей", show=False)
m.add_child(fg)
work_area.explore(m=fg, color='silver', highlight=False, tooltip=False)

fg = folium.FeatureGroup(name="Остановки_ОТ", show=True)
m.add_child(fg)
gdf_ОТ.explore('TrType', m=fg, cmap=['Olive', 'Lime'], legend=False)

for i in range(4):
    fg = folium.FeatureGroup(name=f"Здания v{i}", show=(i==0))
    m.add_child(fg)
    gdf_house[(gdf_house.ver==i)].explore('Code_Type', m=fg, cmap=lambda x: 'blue' if x==2 else 'purple' if x==1 else 'grey', legend=False)

    fg = folium.FeatureGroup(name=f"Пешеходные дорожки v{i}", show=(i==0))
    m.add_child(fg)
    gdf_streets[(gdf_streets.ver==i)&(gdf_streets["ROAD_CATEG"] == "Пешеходные дорожки")].explore(m=fg, color="green")
    
    fg = folium.FeatureGroup(name=f"Дороги v{i}", show=(i==0))
    m.add_child(fg)
    gdf_streets[(gdf_streets.ver==i)&(gdf_streets["Foot"] == 1)&(gdf_streets["ROAD_CATEG"] != "Пешеходные дорожки")].explore(m=fg, color="red")

fg = folium.FeatureGroup(name=f"Сеть для новых дорожек", show=False)
m.add_child(fg)
full_grid_xy.explore(m=fg, color='green')

    
m.add_child(folium.LayerControl())

In [86]:
buf_streets_0 = gdf_streets[gdf_streets.ver>=0].dissolve().buffer(2.51)

In [87]:
# Стороим сеть для покрытия старых дорожек

minx, miny, maxx, maxy = work_area.item().bounds

slice_x = 0
slice_y = 0

param_step = 5

grid_x = []
x = minx + slice_x
while x < maxx:
    grid_x += [x]
    x += param_step

grid_y = []
y = miny + slice_y
while y < maxy:
    grid_y += [y]
    y += param_step

streets_grid_xy = buf_streets_0.intersection(MultiPoint([(x,y) for x in grid_x for y in grid_y]))


In [ ]:
m = folium.Map(location=(55.755826, 37.6173), zoom_start=10, attributionControl=0)
streets_grid_xy.explode(ignore_index=True).reset_index().explore(m=m)

In [37]:
node_streets_0 = streets_grid_xy.explode().map(lambda x: x.coords[0]).apply(pd.Series).rename(columns={0:"x", 1:"y"})

In [41]:
hyppo = 2**0.5
edges = []
for i, row in node_streets_0.iterrows():
    pairs = node_streets_0[node_streets_0.x.between(row.x-param_step-0.001,row.x+param_step+0.001)&node_streets_0.y.between(row.y-param_step-0.001,row.y+param_step+0.001)]
    for p_i, p_row in pairs.iterrows():
        if p_i != i:
            edges.append([i, p_i, 1 if (row.x==p_row.x) or (row.x==p_row.x) else hyppo])
            # break

In [44]:
G = nx.Graph()
G.add_nodes_from(node_streets_0)
G.add_weighted_edges_from(edges)

In [51]:
dist = nx.shortest_path_length(G, source=0, weight='weight')

In [56]:
sh_path = nx.shortest_path(G, source=0, weight='weight')

In [72]:
# nodes_mkd = gdf_house[gdf_house['Apartments']>0]
# nodes_school = gdf_house[gdf_house.Type=='Школы']
# nodes_detsad = gdf_house[gdf_house.Type=='Дошкольные']

In [123]:
# захватываем прилегающую к МКД дорогу
nodes_mkd = gdf_house[gdf_house['Apartments']>0].buffer(15)
nodes_mkd = nodes_mkd.intersection(streets_grid_xy.item())

In [124]:
nodes_mkd

145      MULTIPOINT (1159609.451 6209795.12, 1159614.45...
146      MULTIPOINT (1159684.451 6209765.12, 1159689.45...
147      MULTIPOINT (1159654.451 6209815.12, 1159659.45...
148      MULTIPOINT (1159614.451 6209785.12, 1159619.45...
149      MULTIPOINT (1159669.451 6209720.12, 1159669.45...
                               ...                        
16503    MULTIPOINT (1160699.451 6208600.12, 1160699.45...
16504    MULTIPOINT (1160689.451 6208660.12, 1160694.45...
16505    MULTIPOINT (1160779.451 6208710.12, 1160784.45...
16506    MULTIPOINT (1160754.451 6208630.12, 1160754.45...
16508    MULTIPOINT (1160829.451 6208740.12, 1160829.45...
Length: 181, dtype: geometry

In [128]:
nodes_school = gdf_house[gdf_house.Type=='Школы'].buffer(15)
nodes_school = nodes_school.intersection(streets_grid_xy.item())

In [129]:
nodes_school

1421     MULTIPOINT (1160694.451 6210650.12, 1160694.45...
1422     MULTIPOINT (1160389.451 6210500.12, 1160394.45...
1425     MULTIPOINT (1159399.451 6210120.12, 1159399.45...
1428     MULTIPOINT (1161919.451 6208900.12, 1161924.45...
1429     MULTIPOINT (1159189.451 6209090.12, 1159189.45...
1431     MULTIPOINT (1160914.451 6210335.12, 1160919.45...
1432     MULTIPOINT (1162299.451 6209415.12, 1162304.45...
1434     MULTIPOINT (1161549.451 6209325.12, 1161554.45...
1435     MULTIPOINT (1158999.451 6207480.12, 1159004.45...
16509    MULTIPOINT (1161259.451 6207985.12, 1161259.45...
16510    MULTIPOINT (1160434.451 6207680.12, 1160434.45...
16557    MULTIPOINT (1161234.451 6208300.12, 1161234.45...
16558    MULTIPOINT (1160839.451 6207820.12, 1160844.45...
16559    MULTIPOINT (1160209.451 6208235.12, 1160214.45...
dtype: geometry

In [132]:
nx.shortest_path_length(G, source=16508, target=1421, weight='weight')

1067.0306627408045

In [134]:
str(nx.shortest_path(G, source=16508, target=1421, weight='weight'))

'[16508, 16509, 16510, 16511, 16512, 16549, 16550, 16551, 16593, 16628, 16665, 16694, 16723, 16749, 16775, 16803, 16834, 16864, 16891, 16920, 16956, 16996, 17040, 17092, 17136, 17179, 17216, 17249, 17248, 17215, 17214, 17213, 17212, 17211, 17178, 17177, 17176, 17175, 17174, 17134, 17133, 17132, 17131, 17091, 17090, 17089, 17088, 17087, 17039, 17038, 17037, 17036, 17035, 16995, 16994, 16993, 16992, 16991, 16990, 16989, 16988, 16987, 17034, 17033, 17032, 17086, 17085, 17084, 17127, 17126, 17125, 17124, 17083, 17082, 17081, 17080, 17079, 17078, 17077, 17031, 17030, 17029, 17028, 17027, 17026, 17025, 16986, 16985, 16984, 16983, 16955, 16919, 16890, 16863, 16833, 16802, 16774, 16748, 16722, 16693, 16663, 16627, 16592, 16548, 16495, 16437, 16386, 16353, 16323, 16292, 16256, 16220, 16221, 16181, 16182, 16140, 16102, 16065, 16029, 15992, 15943, 15887, 15888, 15827, 15828, 15764, 15765, 15766, 15767, 15768, 15723, 15724, 15725, 15769, 15770, 15771, 15772, 15773, 15774, 15775, 15776, 15777, 1577

In [139]:
s_path.index

Index([0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       ...
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
      dtype='int64', length=52991)

In [140]:
m = folium.Map(location=(55.755826, 37.6173), zoom_start=10, attributionControl=0)
s_path = streets_grid_xy.explode(ignore_index=True)
s_path[s_path.index.isin(nx.shortest_path(G, source=16508, target=1421, weight='weight'))].explore(m=m)

In [ ]:
m = folium.Map(location=(55.755826, 37.6173), zoom_start=10, attributionControl=0)
nodes_mkd.explode(ignore_index=True).reset_index().explore(m=m)

In [ ]:
145      

# Обучение модели, оценка эффективности и выбор новых пешеходных дорожек

In [ ]:
# Пропускная способность пешеходной дорожки равна 800 чел/ч. Загруженность можно рассчитать по формуле:
# Загруженность = 𝑁 * 𝑃 где 𝑁 - интенсивность движения пешеходов, а 𝑃 - пропускная способность дорожки.

P = 800  # Пропускная способность

# столбебц добавляем загруженности
routes_df['load'] = routes_df['people'] / P

def load_category(load):
    if load > 1:
        return 'Сильно загружена'
    elif load > 0.1:
        return 'Средняя загруженность'
    else:
        return 'Низкая загруженность'

routes_df['load_category'] = routes_df['load'].apply(load_category)

from catboost import CatBoostRegressor

routes_df['start'] = routes_df['start'].astype('category')
routes_df['end'] = routes_df['end'].astype('category')


X = routes_df[['start', 'end', 'nodes', 'people']]
y = routes_df['load']

model = CatBoostRegressor(iterations=1000, depth=6, learning_rate=0.1, loss_function='RMSE', cat_features=['start', 'end'])
model.fit(X, y)

def rationality_score(new_load, existing_load):
    return new_load / existing_load

new_routes_data = {
    'start': ['Home2'], 
    'end': ['School2'],
    'nodes': [2], 
    'people': [50]
}
new_routes_df = pd.DataFrame(new_routes_data)

new_X = new_routes_df[['start', 'end', 'nodes', 'people']]
new_routes_df['new_load'] = model.predict(new_X)

existing_loads = routes_df['load'].values
new_routes_df['rationality'] = new_routes_df['new_load'].apply(lambda x: rationality_score(x, existing_loads.mean()))
new_routes_df['load_category'] = new_routes_df['new_load'].apply(load_category)
new_routes_df
